In [ ]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

import pickle

# Resample the imbalanced dataset

In [2]:
ds= pd.read_csv('prepared_ds/idalia1_prepared_ds_10082024.csv', index_col=0)

#Train, validation, test datasets and balanced mini batch

In [ ]:
from sklearn.model_selection import train_test_split
# Use a utility from sklearn to split and shuffle your dataset.
other_df, test_df = train_test_split(ds, test_size=0.1, random_state=11)
train_df, val_df = train_test_split(other_df, test_size=0.2, random_state=23)

In [ ]:
print(f'Average class probability in training set:   {train_df.flood_mark.mean():.4f}')
print(f'Average class probability in validation set: {val_df.flood_mark.mean():.4f}')
print(f'Average class probability in test set:       {test_df.flood_mark.mean():.4f}')

## Techniques for neuro-net


In [ ]:
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, Dense, Dropout, BatchNormalization, Activation
from tensorflow.keras.models import load_model

import os
import tempfile

import matplotlib as mpl
import seaborn as sns

import sklearn
from sklearn.metrics import confusion_matrix

from sklearn.compose import ColumnTransformer
from sklearn.impute import SimpleImputer
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import FunctionTransformer, OneHotEncoder, StandardScaler


def convert_float64(X):
    return X.astype(np.float64)

In [7]:
mpl.rcParams['figure.figsize'] = (12, 10)
colors = plt.rcParams['axes.prop_cycle'].by_key()['color']

In [9]:
X_train = train_df[train_df.columns[:-1]].reset_index(drop=True)
y_train = train_df[train_df.columns[-1]].reset_index(drop=True)
X_val = val_df[val_df.columns[:-1]].reset_index(drop=True)
y_val = val_df[val_df.columns[-1]].reset_index(drop=True)
X_test = test_df[test_df.columns[:-1]].reset_index(drop=True)
y_test = test_df[test_df.columns[-1]].reset_index(drop=True)

In [10]:
numerical_columns = ["dem", "slope", "aspect", "curvx", "curvy", "fvc", "ndbi", "population", "dist2river", "rain", "x", "y"]
numerical_pipeline = make_pipeline(
    FunctionTransformer(func=convert_float64, validate=False), StandardScaler()
)

categorical_columns = ["lc_grp"]
categorical_pipeline = make_pipeline(
    # SimpleImputer(missing_values=-1, strategy="most_frequent"),
    OneHotEncoder(categories="auto"),
)

preprocessor = ColumnTransformer(
    [
        ("numerical_preprocessing", numerical_pipeline, numerical_columns),
        (
            "categorical_preprocessing",
            categorical_pipeline,
            categorical_columns,
        ),
    ],
    # remainder="drop",
)

# Create an environment variable to avoid using the GPU. This can be changed.
import os

os.environ["CUDA_VISIBLE_DEVICES"] = "-1"


In [11]:
METRICS = [
      keras.metrics.BinaryCrossentropy(name='cross entropy'),  # same as model's loss
      keras.metrics.MeanSquaredError(name='Brier score'),
      keras.metrics.TruePositives(name='tp'),
      keras.metrics.FalsePositives(name='fp'),
      keras.metrics.TrueNegatives(name='tn'),
      keras.metrics.FalseNegatives(name='fn'),
      keras.metrics.BinaryAccuracy(name='accuracy'),
      keras.metrics.Precision(name='precision'),
      keras.metrics.Recall(name='recall'),
      keras.metrics.AUC(name='auc'),
      keras.metrics.AUC(name='prc', curve='PR'), # precision-recall curve
]

In [12]:
early_stopping = tf.keras.callbacks.EarlyStopping(
    monitor='val_prc',
    verbose=1,
    patience=10,
    mode='max',
    restore_best_weights=True)

In [13]:
checkpoint_callback = tf.keras.callbacks.ModelCheckpoint(
    filepath='saved_model10082024/checkpoint_model_idalia1_10082024.keras',
    monitor='val_prc',  # Or any other metric you want to monitor
    mode='max',  # 'max' for accuracy, 'min' for loss
    save_best_only=True
)

### Squential Model -- Can't apply monte carlo dropout with current syntax

In [ ]:
from tensorflow.keras.layers import Activation, BatchNormalization, Dense, Dropout, InputLayer
from tensorflow.keras.models import Sequential


def make_model_deterministic(n_features):
    model = Sequential()
    model.add(InputLayer(input_shape=(n_features,)))
    model.add(Dropout(0.005))
    model.add(Dense(200, kernel_initializer="glorot_normal"))
    model.add(BatchNormalization())
    model.add(Activation("relu"))
    model.add(Dropout(0.5))
    model.add(Dense(100, kernel_initializer="glorot_normal", use_bias=False))
    model.add(BatchNormalization())
    model.add(Activation("relu"))
    model.add(Dropout(0.25))
    model.add(Dense(50, kernel_initializer="glorot_normal", use_bias=False))
    model.add(BatchNormalization())
    model.add(Activation("relu"))
    model.add(Dropout(0.15))
    model.add(Dense(25, kernel_initializer="glorot_normal", use_bias=False))
    model.add(BatchNormalization())
    model.add(Activation("relu"))
    model.add(Dropout(0.1))
    model.add(Dense(1, activation="sigmoid"))

    model.compile(loss="binary_crossentropy", optimizer="adam", metrics=METRICS)

    return model

### Functional API -- Monte Carlo droppout applied

In [14]:
def make_model(n_features):
    inputs = Input(shape=(n_features,))

    x = Dropout(0.05)(inputs, training=True)
    x = Dense(200, kernel_initializer="glorot_normal")(x)
    x = BatchNormalization()(x, training=False)
    x = Activation("relu")(x)
    x = Dropout(0.5)(x, training=False)
    x = Dense(100, kernel_initializer="glorot_normal", use_bias=False)(x)
    x = BatchNormalization()(x, training=False)
    x = Activation("relu")(x)
    x = Dropout(0.25)(x, training=False)
    x = Dense(50, kernel_initializer="glorot_normal", use_bias=False)(x)
    x = BatchNormalization()(x, training=False)
    x = Activation("relu")(x)
    x = Dropout(0.15)(x, training=False)
    x = Dense(25, kernel_initializer="glorot_normal", use_bias=False)(x)
    x = BatchNormalization()(x, training=False)
    x = Activation("relu")(x)
    x = Dropout(0.1)(x, training=False)

    outputs = Dense(1, activation="sigmoid")(x)

    model = Model(inputs=inputs, outputs=outputs)
    model.compile(loss="binary_crossentropy", optimizer="adam", metrics=METRICS)

    return model


### Only use balanced mini batch because it has much higher recall and only train one model for now.

In [15]:
X_local_train = preprocessor.fit_transform(X_train)
y_local_train = y_train.values.ravel()
X_local_val = preprocessor.transform(X_val)
y_local_val = y_val.values.ravel()
X_local_test = preprocessor.transform(X_test)
y_local_test = y_test.values.ravel()

In [16]:
from imblearn.keras import BalancedBatchGenerator

# Expand targets to match model output
y_local_train_expanded = np.expand_dims(y_local_train, axis=-1)
y_local_val_expanded = np.expand_dims(y_local_val, axis=-1)

model = make_model(X_local_train.shape[1])
training_generator = BalancedBatchGenerator(
    X_local_train, y_local_train_expanded, batch_size=64, random_state=42
)

balancedbatch_history = model.fit(training_generator, epochs=100, verbose=1, callbacks=[checkpoint_callback], validation_data=(X_local_val, y_local_val_expanded))
balancedbatch_model = model

Epoch 1/100


C:\Users\Mengj\anaconda3\envs\flood_prediction_social-media\Lib\site-packages\keras\src\trainers\data_adapters\py_dataset_adapter.py:121: UserWarning: Your `PyDataset` class should call `super().__init__(**kwargs)` in its constructor. `**kwargs` can include `workers`, `use_multiprocessing`, `max_queue_size`. Do not pass these arguments to `fit()`, as they will be ignored.
  self._warn_if_super_not_called()


253/253 ━━━━━━━━━━━━━━━━━━━━ 15s 23ms/step - Brier score: 0.1213 - accuracy: 0.8289 - auc: 0.9056 - cross entropy: 0.3859 - fn: 684.5551 - fp: 531.8071 - loss: 0.3859 - prc: 0.9028 - precision: 0.8435 - recall: 0.8066 - tn: 3556.3938 - tp: 3386.9922 - val_Brier score: 0.0620 - val_accuracy: 0.9130 - val_auc: 0.9803 - val_cross entropy: 0.2053 - val_fn: 74.0000 - val_fp: 2734.0000 - val_loss: 0.2053 - val_prc: 0.7656 - val_precision: 0.4237 - val_recall: 0.9645 - val_tn: 27450.0000 - val_tp: 2010.0000
Epoch 2/100
253/253 ━━━━━━━━━━━━━━━━━━━━ 5s 19ms/step - Brier score: 0.0646 - accuracy: 0.9145 - auc: 0.9689 - cross entropy: 0.2218 - fn: 268.6339 - fp: 405.1299 - loss: 0.2218 - prc: 0.9631 - precision: 0.8992 - recall: 0.9316 - tn: 3678.8267 - tp: 3807.1575 - val_Brier score: 0.0503 - val_accuracy: 0.9310 - val_auc: 0.9841 - val_cross entropy: 0.1682 - val_fn: 48.0000 - val_fp: 2178.0000 - val_loss: 0.1682 - val_prc: 0.7918 - val_precision: 0.4832 - val_recall: 0.9770 - val_tn: 28006.00

In [ ]:
# For model/code testing and maintanence purpose
from imblearn.keras import BalancedBatchGenerator

# Expand targets to match model output
y_local_train_expanded = np.expand_dims(y_local_train, axis=-1)
y_local_val_expanded = np.expand_dims(y_local_val, axis=-1)

model = make_model(X_local_train.shape[1])
training_generator = BalancedBatchGenerator(
    X_local_train, y_local_train_expanded, batch_size=64, random_state=42
)

balancedbatch_history = model.fit(training_generator, epochs=2, verbose=1, validation_data=(X_local_val, y_local_val_expanded))
balancedbatch_model = model

Epoch 1/2


C:\Users\Mengj\anaconda3\envs\flood_prediction_social-media\Lib\site-packages\keras\src\trainers\data_adapters\py_dataset_adapter.py:121: UserWarning: Your `PyDataset` class should call `super().__init__(**kwargs)` in its constructor. `**kwargs` can include `workers`, `use_multiprocessing`, `max_queue_size`. Do not pass these arguments to `fit()`, as they will be ignored.
  self._warn_if_super_not_called()


253/253 ━━━━━━━━━━━━━━━━━━━━ 11s 16ms/step - Brier score: 0.1290 - accuracy: 0.8128 - auc: 0.8923 - cross entropy: 0.4045 - fn: 763.1910 - fp: 680.0955 - loss: 0.4045 - prc: 0.8917 - precision: 0.8181 - recall: 0.8126 - tn: 3916.4895 - tp: 3820.1165 - val_Brier score: 0.0481 - val_accuracy: 0.9340 - val_auc: 0.9804 - val_cross entropy: 0.1688 - val_fn: 121.0000 - val_fp: 2008.0000 - val_loss: 0.1688 - val_prc: 0.7576 - val_precision: 0.4943 - val_recall: 0.9419 - val_tn: 28176.0000 - val_tp: 1963.0000
Epoch 2/2
253/253 ━━━━━━━━━━━━━━━━━━━━ 4s 14ms/step - Brier score: 0.0631 - accuracy: 0.9132 - auc: 0.9702 - cross entropy: 0.2183 - fn: 290.6092 - fp: 418.4092 - loss: 0.2183 - prc: 0.9630 - precision: 0.9031 - recall: 0.9279 - tn: 3756.6987 - tp: 3938.1448 - val_Brier score: 0.0530 - val_accuracy: 0.9281 - val_auc: 0.9849 - val_cross entropy: 0.1808 - val_fn: 46.0000 - val_fp: 2273.0000 - val_loss: 0.1808 - val_prc: 0.8038 - val_precision: 0.4727 - val_recall: 0.9779 - val_tn: 27911.000

In [22]:
# best_model = keras.models.load_model('saved_model10082024/checkpoint_model_idalia1_10082024.keras')

In [18]:
# best_model.save('saved_model10082024/checkpoint_model_idalia1_10082024.h5')

In [ ]:
#You can save and load your own trained model
best_model_h5 = load_model('saved_model10082024/checkpoint_model_idalia1_10082024.h5')
best_model_h5.summary()

Model: "functional"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                         ┃ Output Shape                ┃         Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━┩
│ input_layer (InputLayer)             │ (None, 15)                  │               0 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dropout (Dropout)                    │ (None, 15)                  │               0 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense (Dense)                        │ (None, 200)                 │           3,200 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ batch_normalization                  │ (None, 200)                 │             800 │
│ (BatchNormalization)                 │                             │                 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ activation (Activation)              │ (None, 200)                 │               0 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dropout_1 (Dropout)                  │ (None, 200)                 │               0 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_1 (Dense)                      │ (None, 100)                 │          20,000 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ batch_normalization_1                │ (None, 100)                 │             400 │
│ (BatchNormalization)                 │                             │                 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ activation_1 (Activation)            │ (None, 100)                 │               0 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dropout_2 (Dropout)                  │ (None, 100)                 │               0 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_2 (Dense)                      │ (None, 50)                  │           5,000 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ batch_normalization_2                │ (None, 50)                  │             200 │
│ (BatchNormalization)                 │                             │                 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ activation_2 (Activation)            │ (None, 50)                  │               0 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dropout_3 (Dropout)                  │ (None, 50)                  │               0 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_3 (Dense)                      │ (None, 25)                  │           1,250 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ batch_normalization_3                │ (None, 25)                  │             100 │
│ (BatchNormalization)                 │                             │                 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ activation_3 (Activation)            │ (None, 25)                  │               0 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dropout_4 (Dropout)                  │ (None, 25)                  │               0 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_4 (Dense)                      │ (None, 1)                   │              26 │
└──────────────────────────────────────┴─────────────────────────────┴──────────────

 Total params: 30,978 (121.01 KB)

 Trainable params: 30,226 (118.07 KB)

 Non-trainable params: 750 (2.93 KB)

 Optimizer params: 2 (12.00 B)

In [2]:
def plot_metrics(history):
  metrics = ['loss', 'prc', 'precision', 'recall']
  for n, metric in enumerate(metrics):
    name = metric.replace("_"," ").capitalize()
    plt.subplot(2,2,n+1)
    plt.plot(history.epoch, history.history[metric], color=colors[0], label='Train')
    plt.plot(history.epoch, history.history['val_'+metric],
             color=colors[0], linestyle="--", label='Val')
    plt.xlabel('Epoch')
    plt.ylabel(name)
    if metric == 'loss':
      plt.ylim([0, plt.ylim()[1]])
    elif metric == 'auc':
      plt.ylim([0.8,1])
    else:
      plt.ylim([0,1])

    plt.legend()
    plt.show()

In [ ]:
plot_metrics(balancedbatch_history)

In [18]:
balancedbatch_model.load_weights('saved_model10082024/checkpoint_model_idalia1_10082024.keras')

In [16]:
# balancedbatch_model.save('saved_model10082024/checkpoint_mc_model_add_0_25_idalia1_10082024.h5')

In [ ]:
balanced_model_predv1 = best_model_h5.predict(X_local_test, batch_size=64, verbose=0)
balanced_model_predv1

In [ ]:
balanced_model_predv2 = balancedbatch_model.predict(X_local_test, batch_size=64, verbose=0)
balanced_model_predv2

In [ ]:
#test code .prediction (no MC Dropout)
sum(balanced_model_predv1 == balanced_model_predv2) == len(balanced_model_predv1)

In [ ]:
#apply MC Dropout
balancedbatch_model(X_local_test)

<tf.Tensor: shape=(16134, 1), dtype=float32, numpy=
array([[8.5460215e-06],
       [8.6376276e-03],
       [2.8776241e-04],
       ...,
       [6.8050984e-05],
       [4.9580699e-03],
       [9.9984556e-01]], dtype=float32)>

In [ ]:
#Draw samples
y_hat_mc = np.array([balancedbatch_model(X_local_test) for _ in range(2000)])

In [28]:
def plot_cm(labels, predictions, threshold=0.5):
  cm = confusion_matrix(labels, predictions > threshold)
  plt.figure(figsize=(5,5))
  sns.heatmap(cm, annot=True, fmt="d")
  plt.title('Confusion matrix @{:.2f}'.format(threshold))
  plt.ylabel('Actual label')
  plt.xlabel('Predicted label')

  print('Non Flooded Points Detected (True Negatives): ', cm[0][0])
  print('Non Flooded Points Incorrectly Detected (False Positives): ', cm[0][1])
  print('Flooded Points Missed (False Negatives): ', cm[1][0])
  print('Flooded Points Detected (True Positives): ', cm[1][1])
  print('Total Flooded Points: ', np.sum(cm[1]))

In [ ]:
plot_cm(y_local_test, np.mean(y_hat_mc, axis=0).squeeze())

In [ ]:
np.std(y_hat_mc, axis=0).squeeze().mean()

# Make predictions using MC model

### Prepare dataset for prediction:

Most of the input layer were downloaded or calculated from google earth engine.

DEM datasource in the shared drive was resampled to 10 meters.

In [ ]:
# cols = ["coordinates", "id", "elev", "flabel", "slope", "aspect", "curvex", "curvey", "fvc", "ndbi", "landcover", "rain", "population", "dist2river"]
df_predv1 = gpd.read_file("/content/drive/MyDrive/social_media_based_model/model_test/07152024/grid30m_inspection07152024.shp")
# df.columns = cols
df_predv1.dropna().head()

dem    slope     aspect  curvature_  curvatur_1  simple_esa      fvc  \
0  4.43957  0.30876   85.20870     0.17586    -0.01197         2.0  0.47273   
1  4.36276  1.27461  177.35248    -0.21330     0.07581         1.0  0.43633   
2  4.25769  0.29232  174.67653     0.29209    -0.44655         1.0  0.72432   
3  4.02727  0.53895   93.78531    -0.21337     0.07409         2.0  0.10234   
4  4.33231  0.47361  298.55835    -0.07294     0.31866         2.0  0.32793   

      ndbi  population  dist2river  rain_idali                    geometry  
0 -0.01085     2.36280        34.0     33.2329  POINT (-82.77158 27.92079)  
1 -0.09858    23.43978        34.0     33.2329  POINT (-82.77158 27.92049)  
2 -0.10734    23.43978        34.0     33.2329  POINT (-82.77158 27.92019)  
3  0.07016    18.90984        34.0     33.2329  POINT (-82.77158 27.91989)  
4 -0.03505   142.95651        34.0     33.2329  POINT (-82.77158 27.91959)

In [ ]:
df_predv1 = df_predv1[df_predv1.simple_esa.isin([0., 1., 2.])].dropna().reset_index(drop=True)
df_predv1.shape

(310738, 12)

In [ ]:
coord_list_predv1 = [(x,y) for x,y in zip(df_predv1['geometry'].x , df_predv1['geometry'].y)]

In [ ]:
df_predv1['x'] = pd.DataFrame(coord_list_predv1)[0]
df_predv1['y'] = pd.DataFrame(coord_list_predv1)[1]

In [ ]:
df_predv1 = df_predv1[["dem", "slope", "aspect", "curvature_", "curvatur_1", "simple_esa", "fvc", "ndbi", "population", "dist2river", "rain_idali", "x", "y"]]
cols_predv1 = ["dem", "slope", "aspect", "curvx", "curvy", "lc_grp", "fvc", "ndbi", "population", "dist2river", "rain", "x", "y"]
df_predv1.columns = cols_predv1
df_predv1.head()

dem    slope     aspect    curvx    curvy  lc_grp      fvc     ndbi  \
0  4.43957  0.30876   85.20870  0.17586 -0.01197     2.0  0.47273 -0.01085   
1  4.36276  1.27461  177.35248 -0.21330  0.07581     1.0  0.43633 -0.09858   
2  4.25769  0.29232  174.67653  0.29209 -0.44655     1.0  0.72432 -0.10734   
3  4.02727  0.53895   93.78531 -0.21337  0.07409     2.0  0.10234  0.07016   
4  4.33231  0.47361  298.55835 -0.07294  0.31866     2.0  0.32793 -0.03505   

   population  dist2river     rain          x          y  
0     2.36280        34.0  33.2329 -82.771576  27.920787  
1    23.43978        34.0  33.2329 -82.771576  27.920487  
2    23.43978        34.0  33.2329 -82.771576  27.920187  
3    18.90984        34.0  33.2329 -82.771576  27.919887  
4   142.95651        34.0  33.2329 -82.771576  27.919587

In [ ]:
df_predv1.lc_grp = pd.Categorical(df_predv1.lc_grp)

In [ ]:
df_predv1.dtypes

dem            float64
slope          float64
aspect         float64
curvx          float64
curvy          float64
lc_grp        category
fvc            float64
ndbi           float64
population     float64
dist2river     float64
rain           float64
x              float64
y              float64
dtype: object

In [ ]:
df_predv1.describe().columns

Index(['dem', 'slope', 'aspect', 'curvx', 'curvy', 'fvc', 'ndbi', 'population',
       'dist2river', 'rain', 'x', 'y'],
      dtype='object')

In [ ]:
preprocessor

ColumnTransformer(transformers=[('numerical_preprocessing',
                                 Pipeline(steps=[('functiontransformer',
                                                  FunctionTransformer(func=<function convert_float64 at 0x7c098d083d90>)),
                                                 ('standardscaler',
                                                  StandardScaler())]),
                                 ['dem', 'slope', 'aspect', 'curvx', 'curvy',
                                  'fvc', 'ndbi', 'population', 'dist2river',
                                  'rain', 'x', 'y']),
                                ('categorical_preprocessing',
                                 Pipeline(steps=[('onehotencoder',
                                                  OneHotEncoder())]),
                                 ['lc_grp'])])

In [ ]:
X_ds = ds[ds.columns[:-1]].reset_index(drop=True)
X_predv1 = df_predv1[df_predv1.y<27.85].reset_index(drop=True)
X_local_predv1 = preprocessor.fit(X_train).transform(X_predv1)

In [ ]:
y_hat_mc_predv1 = np.array([balancedbatch_model(X_local_predv1) for _ in range(2000)])

In [ ]:
MC_pred_meanv1 = np.mean(y_hat_mc_predv1, axis=0).squeeze()
MC_pred_stdv1 = np.std(y_hat_mc_predv1, axis=0).squeeze()

In [ ]:
y_hat_simple_mcv1 = pd.DataFrame({'MC_pred_mean': MC_pred_meanv1, 'MC_pred_std': MC_pred_stdv1})
y_hat_simple_mcv1.head()

pred
0  0.999319
1  0.999480
2  0.999448
3  0.999487
4  0.999480

## Continue of uncertainty analysis

In [ ]:
y_hat_simple_mcv1['x'] = X_predv1.x.values
y_hat_simple_mcv1['y'] = X_predv1.y.values
# y_hat_simple_mc_gpd = gpd.GeoDataFrame(
#     y_hat_simple_mc, geometry=gpd.points_from_xy(y_hat_simple_mc.x, y_hat_simple_mc.y), crs="EPSG:4269"
#     )
# y_hat_simple_mc_gpd.head()

# Visualize predictions in new areas

In [ ]:
f = open("google_map_api.txt", "r")
GOOGLE_API_KEY = f.read()
f.close()

In [ ]:
from bokeh.io import output_notebook
output_notebook()
bokeh_width, bokeh_height = 700,560

In [ ]:
# Location PINELLAS COUNTY    Latitude  27.90268000    Longitude  -82.73955000
lat, lon = 27.90268000, -82.73955000

In [ ]:
import os
api_key = GOOGLE_API_KEY

In [ ]:
from bokeh.io import show
from bokeh.plotting import gmap
from bokeh.models import GMapOptions

from bokeh.models import ColumnDataSource
from bokeh.models import HoverTool

from bokeh.transform import linear_cmap
from bokeh.palettes import Plasma256
from bokeh.models import ColorBar

In [ ]:
def plot(lat, lng, zoom=10, map_type='roadmap'):
    gmap_options = GMapOptions(lat=lat, lng=lng,
                               map_type=map_type, zoom=zoom)
    p = gmap(api_key, gmap_options, title='Pinellas County',
             width=bokeh_width, height=bokeh_height)
    show(p)
    return p

In [ ]:
p = plot(lat, lon)

In [ ]:
# Read the shapefile
flood_img2polygon = gpd.read_file('/content/drive/MyDrive/social_media_based_model/adds_data_run_model070424/flooding_add1.shp')

# Function to extract x and y coordinates from the geometries
def extract_coords(geometry):
    if geometry.geom_type == 'Polygon':
        exterior_coords = geometry.exterior.coords.xy
        return list(exterior_coords[0]), list(exterior_coords[1])
    elif geometry.geom_type == 'MultiPolygon':
        xs, ys = [], []
        for polygon in geometry:
            exterior_coords = polygon.exterior.coords.xy
            xs.append(list(exterior_coords[0]))
            ys.append(list(exterior_coords[1]))
        return xs, ys

# Extract coordinates for all polygons
polygon_xs, polygon_ys = [], []
for geom in flood_img2polygon.geometry:
    xs, ys = extract_coords(geom)
    polygon_xs.append(xs)
    polygon_ys.append(ys)

# Prepare the data for ColumnDataSource
flood_img2polygon['polygon_xs'] = polygon_xs
flood_img2polygon['polygon_ys'] = polygon_ys


In [ ]:
def plot(lat, lng, zoom=10, map_type='roadmap'):
    gmap_options = GMapOptions(lat=lat, lng=lng,
                               map_type=map_type, zoom=zoom)
    # the tools are defined below:
    hover = HoverTool(
        tooltips = [
            ('mean flooding probability', '@MC_pred_mean'),
            ('std of mc samples', '@MC_pred_std')
        ]
    )
    # below we replaced 'hover' (the default hover tool),
    # by our custom hover tool
    p = gmap(api_key, gmap_options, title='Monte Carlo Dropout to Measure Flood Prediction Uncertainty',
             width=bokeh_width, height=bokeh_height,
             tools=[hover, 'reset', 'wheel_zoom', 'pan'])
    source = ColumnDataSource(y_hat_simple_mcv1[y_hat_simple_mcv1.y<27.85])

    mapper = linear_cmap('MC_pred_mean', Plasma256[::-1], 0., 1.)
    # print(mapper)
    # we use the mapper for the color of the circles
    center = p.scatter('x', 'y', size='radius', alpha=0.7,
                      color=mapper, source=source)
    # and we add a color scale to see which values the colors
    # correspond to
    color_bar = ColorBar(color_mapper=mapper['transform'],
                         location=(0,0))
    p.add_layout(color_bar, 'right')

    # Add polygon layer
    flood_img = ColumnDataSource(data=dict(
        polygon_xs=flood_img2polygon.polygon_xs,
        polygon_ys=flood_img2polygon.polygon_ys,
    ))

    p.patches('polygon_xs', 'polygon_ys', source=flood_img, fill_color='cyan', fill_alpha=0.3, line_color='navy')

    show(p)
    return p

p = plot(lat, lon, map_type='roadmap', zoom=10)